# Calculating full frame averages from .tif files
* 3/16/24 setup
* 4/11/2024 migrated from lab3 repo. Making it compatible with dendritic data.
* this is in shamble. that calculation with the 'SequenceIndex' throws stuff off

In [1]:
import os
from os.path import join
import re

import tifffile as tf
import pandas as pd
import numpy as np

import plotly.express as px
import plotly.graph_objects as go

from src import full_frame_analysis as ffa

In [2]:
sima_dir = "/data2/gergely/invivo_DATA/sleep/dock11c5/8_2/TSeries-08022024-1036-001/TSeries-08022024-1036-001.sima/"
directories = []
pattern = re.compile(r"plane\d+")

for root, dirs, files in os.walk(sima_dir):
    for dir_name in dirs:
        if pattern.match(dir_name):
            reg_tif_dir = os.path.join(root, dir_name, "reg_tif")
            if os.path.exists(reg_tif_dir):
                directories.append(reg_tif_dir)

print(directories)


['/data2/gergely/invivo_DATA/sleep/dock11c5/8_2/TSeries-08022024-1036-001/TSeries-08022024-1036-001.sima/s2p_ff/suite2p/plane1/reg_tif', '/data2/gergely/invivo_DATA/sleep/dock11c5/8_2/TSeries-08022024-1036-001/TSeries-08022024-1036-001.sima/s2p_ff/suite2p/plane0/reg_tif']


In [16]:
# Initialize a list to hold the ca_data
ca_data = []

# Iterate through the directories and process TIFF files
for directory in directories:
    plane_name = os.path.basename(
        os.path.dirname(directory)
    )  # Extract the plane name (e.g., 'plane0')
    file_count = 0
    frame_count = 0

    # Iterate over files in the directory
    for filename in os.listdir(directory):
        if filename.endswith(
            "_chan0.tif"
        ):  # Check if the file is a TIFF file of interest
            file_count += 1
            file_path = os.path.join(directory, filename)
            with tf.TiffFile(file_path) as tif:
                for page in tif.pages:
                    frame_count += 1
                    # Convert the current frame/page to a numpy array
                    image = page.asarray()
                    # Calculate the average pixel value for the frame
                    avg_pixel_value = np.mean(image)
                    # Append the file name, frame index, average pixel value, and plane information to the data list
                    ca_data.append(
                        {
                            "File": filename,
                            "Frame": frame_count,
                            "AveragePixelValue": avg_pixel_value,
                            "Plane": plane_name,
                        }
                    )

# Convert the list to a pandas DataFrame
ca_df = pd.DataFrame(ca_data)

# Debugging information
print(f"DataFrame length: {len(ca_df)}")
print(f"DataFrame head:\n{ca_df.head()}")


DataFrame length: 40750
DataFrame head:
                File  Frame  AveragePixelValue   Plane
0  file009_chan0.tif      1         277.594578  plane1
1  file009_chan0.tif      2         277.016640  plane1
2  file009_chan0.tif      3         282.602951  plane1
3  file009_chan0.tif      4         281.649712  plane1
4  file009_chan0.tif      5         280.378368  plane1


In [21]:
ca_df.to_csv(join(sima_dir, "s2p_ff", "ff_ca_data.csv"), index=False)

In [20]:
# Sort the DataFrame by 'File', 'Frame', and 'Plane' if not already sorted
# ca_df.sort_values(by=["File", "Frame", "Plane"], inplace=True)

# Create a new column 'SequenceIndex' that uniquely identifies each frame in the sequence
# ca_df["SequenceIndex"] = range(len(ca_df))

# Create separate plots for plane0 and plane1 using Plotly
fig = go.Figure()

for plane, color in zip(["plane0", "plane1"], ["blue", "red"]):
    plane_data = ca_df[ca_df["Plane"] == plane]
    fig.add_trace(
        go.Scatter(
            # x=plane_data["SequenceIndex"],
            y=plane_data["AveragePixelValue"],
            mode="lines",
            name=f"{plane.capitalize()} Average Pixel Value",
            line=dict(color=color),
        )
    )

fig.update_layout(
    title="Average Pixel Value per Frame for Plane0 and Plane1",
    # xaxis_title="Sequence Index",
    yaxis_title="Average Pixel Value",
    template="plotly_white",
)

fig.show()


In [69]:
try:
    eeg_data = pd.read_csv(join(sima_dir, "eeg/velo_eeg.csv"))
    nrem_data = eeg_data["NREM"]
    ca_df["NREM"] = nrem_data
except FileNotFoundError:
    print("No EEG data found")
    mob_immob_data = pd.read_json(join(sima_dir, "behavior/mobility_immobility.json"))
    ca_df["mob_immob"] = mob_immob_data

No EEG data found


### something looks fishy with this calcualtion. the signal has that very wird periodicity. 

In [22]:
# Parameters
window_size = 5000  # Define your window size here
percentile = 10  # We're using the 10th percentile

# Step 1 & 2: Calculate the rolling percentile as the baseline
# Use 'min_periods=1' to ensure the calculation is done even if the window is not fully populated (e.g., at the start)
ca_df["Baseline"] = (
    ca_df["AveragePixelValue"]
    .rolling(window=window_size, min_periods=100, center=True)
    .apply(lambda x: np.percentile(x, percentile), raw=True)
)

# Step 5: Calculate Delta F/F
ca_df["DeltaF_F"] = (ca_df["AveragePixelValue"] - ca_df["Baseline"]) / ca_df["Baseline"]

# Plotting Delta F/F with Plotly
fig = px.line(
    ca_df,
    x="SequenceIndex",
    y="DeltaF_F",
    title="ΔF/F Trace with Sliding Window Baseline",
    labels={"DeltaF_F": "ΔF/F", "SequenceIndex": "Sequence Index"},
)
# baseline plot:
# fig.add_scatter(
#     x=ca_df["SequenceIndex"],
#     y=ca_df["Baseline"],
#     name="Baseline",
#     mode="lines",
#     line=dict(color="firebrick", width=2, dash="dash"),
# )
fig.show()

In [71]:
# Parameters
cutoff = 0.1  # Cutoff frequency in Hz (take 0.1 as default)
fs = 10  # Sampling rate in Hz (adjust this according to your actual sampling rate)
order = 5  # Filter order (you can adjust this based on your requirements)

# Apply the filter
ca_df["FilteredAveragePixelValue"] = ffa.butter_lowpass_filter(
    ca_df["DeltaF_F"], cutoff, fs, order
)

In [72]:
# Create a figure with secondary y-axis
fig = go.Figure()

# Add ΔF/F trace
fig.add_trace(
    go.Scatter(
        x=ca_df["SequenceIndex"],
        y=ca_df["FilteredAveragePixelValue"],
        name="low pass ΔF/F",
        line=dict(color="blue", width=2),
    )
)

# # Add Baseline trace
# fig.add_trace(
#     go.Scatter(
#         x=ca_df["SequenceIndex"],
#         y=ca_df["Baseline"],
#         name="Baseline",
#         line=dict(color="firebrick", width=2, dash="dash"),
#     )
# )

try:
    # Add NREM trace
    fig.add_trace(
        go.Scatter(
            x=ca_df["SequenceIndex"],
            y=ca_df["NREM"],
            name="NREM",
            line=dict(color="green", width=2),
            yaxis="y2",
        )
    )
except KeyError:
    fig.add_trace(
        go.Scatter(
            x=ca_df["SequenceIndex"],
            y=ca_df["mob_immob"],
            name="mob_immob",
            line=dict(color="green", width=2),
            yaxis="y2",
        )
    )

# Create axis objects
fig.update_layout(
    title="ΔF/F Trace with NREM Overlay",
    xaxis_title="Sequence Index",
    yaxis_title="ΔF/F",
    yaxis=dict(
        title="ΔF/F",
        titlefont=dict(color="blue"),
        tickfont=dict(color="blue"),
    ),
    yaxis2=dict(
        title="NREM",
        titlefont=dict(color="green"),
        tickfont=dict(color="green"),
        anchor="x",
        overlaying="y",
        side="right",
    ),
)

# Show the plot
fig.show()

In [11]:
sorted_df = ca_df.sort_values(by=["File", "Frame", "Plane"], inplace=True)


In [15]:
ca_df.to_csv(join(sima_dir, "ca_data.csv"))

In [12]:
sorted_df